In [2]:
%%bash
# install the vall-e and required libraries
# PyTorch
pip install torch==1.13.1 torchaudio==0.13.1 --extra-index-url https://download.pytorch.org/whl/cu116
pip install torchmetrics==0.11.1
# fbank
pip install librosa matplotlib

# phonemizer pypinyin
apt-get install espeak-ng -y
## OSX: brew install espeak
pip install phonemizer==3.2.1 pypinyin==0.48.0

pip install lhotse

# k2
# find the right version in https://huggingface.co/csukuangfj/k2
pip install https://huggingface.co/csukuangfj/k2/resolve/main/cuda/k2-1.23.4.dev20230224+cuda11.7.torch1.13.1-cp310-cp310-linux_x86_64.whl
mkdir tmp

git clone https://github.com/k2-fsa/icefall
mv icefall tmp
cd tmp/icefall
pip install -r requirements.txt
pip install -e .
export PYTHONPATH=`pwd`/../icefall:$PYTHONPATH
echo "export PYTHONPATH=`pwd`/../icefall:\$PYTHONPATH" >> ~/.zshrc
echo "export PYTHONPATH=`pwd`/../icefall:\$PYTHONPATH" >> ~/.bashrc
cd ../..
source ~/.zshrc
source ~/.bashrc


git clone https://github.com/lifeiteng/vall-e
mv vall-e tmp
cd tmp/vall-e
pip install -e .

pip install vocos

Looking in indexes: https://pypi.org/simple, https://download.pytorch.org/whl/cu116



[notice] A new release of pip is available: 23.1.2 -> 23.2.1
[notice] To update, run: python -m pip install --upgrade pip



[notice] A new release of pip is available: 23.1.2 -> 23.2.1
[notice] To update, run: python -m pip install --upgrade pip



[notice] A new release of pip is available: 23.1.2 -> 23.2.1
[notice] To update, run: python -m pip install --upgrade pip


Reading package lists...
Building dependency tree...
Reading state information...


...


[notice] A new release of pip is available: 23.1.2 -> 23.2.1
[notice] To update, run: python -m pip install --upgrade pip



[notice] A new release of pip is available: 23.1.2 -> 23.2.1
[notice] To update, run: python -m pip install --upgrade pip


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 103.1/103.1 MB 29.2 MB/s eta 0:00:00



[notice] A new release of pip is available: 23.1.2 -> 23.2.1
[notice] To update, run: python -m pip install --upgrade pip
mkdir: cannot create directory ‘tmp’: File exists
Cloning into 'icefall'...
fetch-pack: unexpected disconnect while reading sideband packet


Process is interrupted.


In [2]:
!wget https://huggingface.co/LearnItAnyway/vall-e_korean/resolve/main/vall-e_ko_v0.pt
!wget https://huggingface.co/LearnItAnyway/vall-e_korean/resolve/main/unique_text_tokens.k2symbols

--2023-09-21 06:28:48--  https://huggingface.co/LearnItAnyway/vall-e_korean/resolve/main/vall-e_ko_v0.pt
Resolving huggingface.co (huggingface.co)... 13.32.110.77, 13.32.110.109, 13.32.110.28, ...
Connecting to huggingface.co (huggingface.co)|13.32.110.77|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://cdn-lfs.huggingface.co/repos/f8/b9/f8b90061950052a23944dd83f71a6f031a5d39c73dbb799693620ca8a4186a97/e2894775b160c24132f8f6d6d7df6cc8bf59a9b465778d08989e200859610560?response-content-disposition=attachment%3B+filename*%3DUTF-8%27%27vall-e_ko_v0.pt%3B+filename%3D%22vall-e_ko_v0.pt%22%3B&Expires=1695536928&Policy=eyJTdGF0ZW1lbnQiOlt7IkNvbmRpdGlvbiI6eyJEYXRlTGVzc1RoYW4iOnsiQVdTOkVwb2NoVGltZSI6MTY5NTUzNjkyOH19LCJSZXNvdXJjZSI6Imh0dHBzOi8vY2RuLWxmcy5odWdnaW5nZmFjZS5jby9yZXBvcy9mOC9iOS9mOGI5MDA2MTk1MDA1MmEyMzk0NGRkODNmNzFhNmYwMzFhNWQzOWM3M2RiYjc5OTY5MzYyMGNhOGE0MTg2YTk3L2UyODk0Nzc1YjE2MGMyNDEzMmY4ZjZkNmQ3ZGY2Y2M4YmY1OWE5YjQ2NTc3OGQwODk4OWUyMDA4NTk2MTA1NjA%7

In [1]:
import argparse
import logging
import os
import pathlib
import time
import tempfile
import platform
import webbrowser
import sys
import torch, torchaudio
import random

import numpy as np

from valle.data import (
    AudioTokenizer,
    TextTokenizer,
    tokenize_audio,
    tokenize_text
)
from icefall.utils import AttributeDict
from valle.data.collation import get_text_token_collater
from valle.models import get_model

from vocos import Vocos
from encodec.utils import convert_audio
import multiprocessing

thread_count = multiprocessing.cpu_count()

print("Use",thread_count,"cpu cores for computing")

torch.set_num_threads(thread_count)
torch.set_num_interop_threads(thread_count)
torch._C._jit_set_profiling_executor(False)
torch._C._jit_set_profiling_mode(False)
torch._C._set_graph_executor_optimize(False)

text_tokenizer = TextTokenizer(language='ko')

device = torch.device("cpu")
if torch.cuda.is_available():
    device = torch.device("cuda", 0)

checkpoint = torch.load("./vall-e_ko_v0.pt", map_location='cpu')
model = get_model(AttributeDict(checkpoint))
missing_keys, unexpected_keys = model.load_state_dict(
    checkpoint["model"], strict=True
)
assert not missing_keys
model.eval()
model.to(device)
text_collater = get_text_token_collater('./unique_text_tokens.k2symbols')

# Encodec model
audio_tokenizer = AudioTokenizer(device)

# Vocos decoder
vocos = Vocos.from_pretrained('charactr/vocos-encodec-24khz').to(device)

model.to(device)
@torch.no_grad()
def infer_from_prompt(text_prompt, audio_prompt, text):
    ## text to token
    text_tokens, text_tokens_lens = text_collater(
        [
            tokenize_text(
                text_tokenizer, text=f"{text_prompt} {text}".strip()
            )
        ]
    )
    _, enroll_x_lens = text_collater(
        [
            tokenize_text(
                text_tokenizer, text=f"{text_prompt}".strip()
            )
        ]
    )
    print('text_loaded')

    # text to synthesize
    wav_pr, sr = torchaudio.load(audio_prompt)
    wav_pr = convert_audio(wav_pr, sr, audio_tokenizer.sample_rate, audio_tokenizer.channels)
    audio_prompts = audio_tokenizer.encode(wav_pr.unsqueeze(0))[0][0].transpose(2, 1).to(device)
    print('Audio encoded')

    encoded_frames = model.inference(
        text_tokens.to(device), text_tokens_lens.to(device),
        audio_prompts, enroll_x_lens=enroll_x_lens,
        top_k=-100, temperature=1)
    vocos_features = vocos.codes_to_features(encoded_frames.permute(2, 0, 1))
    samples = vocos.decode(vocos_features, bandwidth_id=torch.tensor([2], device=device))
    message = f"sythesized text: {text}"
    return message, (24000, samples.squeeze(0).cpu().numpy())


Use 32 cpu cores for computing


Downloading: "https://dl.fbaipublicfiles.com/encodec/v0/encodec_24khz-d7cc33bc.th" to /root/.cache/torch/hub/checkpoints/encodec_24khz-d7cc33bc.th


  0%|          | 0.00/88.9M [00:00<?, ?B/s]

# Example

In [ ]:
text_prompt = '' # text of the audio 
audio_prompt = '' # path to the audio file
text = '' # 
message, (sr, data) = infer_from_prompt(text_prompt, audio_prompt, text)

In [ ]:
print(message)
from IPython.display import Audio
Audio(data, rate=sr)

# Simple Gradio App

In [3]:
!pip install gradio

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 20.2/20.2 MB 12.7 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 520.6/520.6 kB 16.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 66.2/66.2 kB 19.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 298.2/298.2 kB 22.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.7/75.7 kB 23.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 138.7/138.7 kB 35.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.3/12.3 MB 16.3 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 374.5/374.5 kB 26.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.7/45.7 kB 17.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.5/59.5 kB 22.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 129.9/129.9 kB 45.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 502.

In [4]:
import gradio as gr
app = gr.Blocks(title="VALL-E Korean")
with app:
    #gr.Markdown(top_md)
    with gr.Tab("VALL-E Korean Demo"):
        #gr.Markdown(infer_from_prompt_md)
        with gr.Row():
            with gr.Column():
                text_prompt = gr.TextArea(label="Input Text",
                                      placeholder="Type text in the audio file (Korean)",)
                audio_prompt= gr.Audio(label="Input Audio", source='upload', interactive=True, type="filepath")
                text_input = gr.TextArea(label="Output Text",
                                      placeholder="Type text you want to generate (Korean)",)
            with gr.Column():
                text_output = gr.Textbox(label="Message")
                audio_output= gr.Audio(label="Output Audio")
                btn = gr.Button("Generate!")
                btn.click(infer_from_prompt,
                          inputs=[text_prompt, audio_prompt, text_input],
                          outputs=[text_output, audio_output])
webbrowser.open("http://127.0.0.1:7860")
app.launch(share=True)

Running on local URL:  http://127.0.0.1:7860
Running on public URL: https://e3c6ff480c5537ff44.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)
